# Data Cleaning: Salary

In [2]:
import pandas as pd
import re 
import numpy as np
import seaborn as sns
import matplotlib.pyplot as plt

In [4]:
df = pd.read_csv("final_sorted_job_titles_date.csv")

In [12]:
df.columns

Index(['Job Title', 'Company', 'Location', 'Salary Min', 'Salary Max',
       'Description', 'Extracted Skills', 'Longitude', 'Latitude', 'URL',
       'Created', 'Experience_years', 'Experience_Level', ' Apache Airflow',
       ' Azure', ' Big Data', ' Data Pipelines', ' Deep Learning', ' Docker',
       ' ETL', ' GCP', ' Hadoop', ' Java', ' KPI', ' Kafka', ' Kubernetes',
       ' Machine Learning', ' Pandas', ' Power BI', ' PyTorch', ' Python',
       ' R', ' SQL', ' Scikit-Learn', ' Snowflake', ' Spark', ' Tableau',
       ' TensorFlow', 'AWS', 'Apache Airflow', 'Azure', 'Big Data',
       'Data Pipelines', 'Deep Learning', 'Docker', 'ETL', 'GCP',
       'Google Analytics', 'Hadoop', 'Java', 'KPI', 'Kafka', 'Kubernetes',
       'Machine Learning', 'Pandas', 'Power BI', 'PyTorch', 'Python', 'R',
       'SQL', 'Snowflake', 'Spark', 'Tableau', 'TensorFlow'],
      dtype='object')

In [5]:
# Identifying Anomalous Salary Values
low_salaries = df[(df["Salary Min"] < 1000) | (df["Salary Max"] < 1000)]
low_salaries

Job Title                           Company  \
24                Data Engineer        SRA Information Technology   
58                Data Engineer                           HCLTech   
59                Data Engineer                       InfoCentric   
60               Data Scientist          Cevo trades as Cevo  Pty   
61               Data Scientist          Cevo trades as Cevo  Pty   
62               Data Scientist          Cevo trades as Cevo  Pty   
80               Data Scientist                           Innablr   
81               Data Scientist                  News Corporation   
86                Data Engineer                           intelia   
88                Data Engineer                VIS Global Pty Ltd   
89                Data Engineer                    Allurapartners   
90                Data Engineer                    Allurapartners   
183        Analytics Consultant                        Mastercard   
280   Machine Learning Engineer                       InfoCentric   
362              Data Scientist                 Commonwealth Bank   
363   Machine Learning Engineer        Interface Agency Australia   
365   Machine Learning Engineer                     Equifax, Inc.   
366   Machine Learning Engineer                     Equifax, Inc.   
369   Machine Learning Engineer        Kaizen Global Technologies   
384              Data Scientist                         Digimatch   
385              Data Scientist                 Jinane Consulting   
387              Data Scientist          Phaidon London- Glocomms   
388              Data Scientist                         AVALIANCE   
397              Data Scientist                             APRIL   
398              Data Scientist                        Canal Plus   
401              Data Scientist                        Canal Plus   
403              Data Scientist                         Framatome   
404              Data Scientist                    Groupe Aptenia   
800               Data Engineer  Just People Information Security   
806               Data Engineer             The Talent Initiative   
807               Data Engineer               Infinite Consulting   
808               Data Engineer         itelligence North America   
836               Data Engineer                       W Recruiter   
1350              Data Engineer                               NaN   
1356              Data Engineer            Jordan Human Resources   
1361  Machine Learning Engineer                              Mseq   
1362  Machine Learning Engineer                     AI Talent pty   
1363  Machine Learning Engineer                             Block   
1415  Machine Learning Engineer      CES Information Technologies   
1417  Machine Learning Engineer           SIlverPeople Consulting   
1629  Machine Learning Engineer            V R Della Infotech Inc   
2343              Data Engineer                               NaN   

                             Location  Salary Min  Salary Max  \
24             Barton, South Canberra       150.0       200.0   
58                  The Rocks, Sydney       150.0       200.0   
59          Dunnstown, Moorabool Area       150.0       200.0   
60          Dunnstown, Moorabool Area       200.0       250.0   
61                  The Rocks, Sydney       200.0       250.0   
62          Dunnstown, Moorabool Area       200.0       250.0   
80          Dunnstown, Moorabool Area       150.0       200.0   
81                  The Rocks, Sydney       200.0       250.0   
86          Dunnstown, Moorabool Area       150.0       200.0   
88          Dunnstown, Moorabool Area       150.0       200.0   
89                  The Rocks, Sydney       150.0       200.0   
90                  The Rocks, Sydney       150.0       200.0   
183         Dunnstown, Moorabool Area       200.0       250.0   
280         Dunnstown, Moorabool Area       150.0       200.0   
362                 The Rocks, Sydney       150.0       200.0   
363         Du

In [6]:
# Step 1: Fix incorrect salary scales (multiply by 1,000)
salaries_to_correct = [90, 120, 135, 145, 150, 190, 200, 250]
df.loc[df["Salary Min"].isin(salaries_to_correct), "Salary Min"] *= 1000
df.loc[df["Salary Max"].isin(salaries_to_correct), "Salary Max"] *= 1000

In [7]:
# Check if Step 1 has been adjusted: YES!
low_salaries = df[(df["Salary Min"] < 1000) | (df["Salary Max"] < 1000)]
low_salaries

Job Title                           Company  \
384              Data Scientist                         Digimatch   
385              Data Scientist                 Jinane Consulting   
387              Data Scientist          Phaidon London- Glocomms   
388              Data Scientist                         AVALIANCE   
397              Data Scientist                             APRIL   
398              Data Scientist                        Canal Plus   
401              Data Scientist                        Canal Plus   
403              Data Scientist                         Framatome   
404              Data Scientist                    Groupe Aptenia   
800               Data Engineer  Just People Information Security   
836               Data Engineer                       W Recruiter   
1350              Data Engineer                               NaN   
1356              Data Engineer            Jordan Human Resources   
1415  Machine Learning Engineer      CES Information Technologies   
1417  Machine Learning Engineer           SIlverPeople Consulting   
1629  Machine Learning Engineer            V R Della Infotech Inc   
2343              Data Engineer                               NaN   

                           Location  Salary Min  Salary Max  \
384           Ile-de-France, France       400.0       600.0   
385               Montrouge, Antony       100.0       570.0   
387            Paris, Ile-de-France       400.0       550.0   
388               Montrouge, Antony       400.0       550.0   
397          Caluire-et-Cuire, Lyon       486.0      1802.0   
398               Puteaux, Nanterre       486.0      1802.0   
401               Puteaux, Nanterre       486.0      1802.0   
403     Rhône, Auvergne-Rhône-Alpes       486.0      1802.0   
404           Ile-de-France, France       600.0       650.0   
800       Brisbane, Brisbane Region         0.0    286000.0   
836           Nord, Hauts-De-France       480.0       520.0   
1350          Johannesburg, Gauteng         0.0     13200.0   
1356             Centurion, Tshwane        36.0        36.0   
1415           Hyderabad, Telangana         0.0   1500000.0   
1417            Mumbai, Maharashtra         0.0   2700000.0   
1629  Sunnyvale, Santa Clara County         2.0        61.0   
2343          Johannesburg, Gauteng         0.0     13200.0   

                                            Description Extracted Skills  \
384   Nous recherchons un Data Scientist pour renfor...               []   
385   Objectifs/Descriptif de mission : Les principa...               []   
387   Proposer des solutions techniques pour répondr...               []   
388   Nous recherchons pour notre client basé à Mont...               []   
397   Venez extraire, analyser et développer des alg...               []   
398   Plus précisément, vous intégrerez la direction...               []   
401   Plus précisément, vous intégrerez la direction...               []   
403   Framatome souhaite étendre sa capacité à trait...               []   
404   Vous rejoindrez l'équipe Global IT (GIT), qui ...               []   
800   You will be a key part of delivering high qual...               []   
836   Votre rôle En tant que Data Engineer Snowflake...               []   
1350  Join a leading company pioneering the power of...               []   
1356  A client in the automobile industry is looking...               []   
1415  o Critical thinking mind who likes to solve co...               []   
1417  ML Engineer-Analyst/ Senior Analyst Job purpos...               []   
1629  Description: Description Job Title EA ML Engin...               []   
2343  Join a leading company pioneering the power of...               []   

       Longitude   Latitude  \
384     2.351634  48.811332   
385     2.319930  48.818460   
387     2.344631  48.863839   
388     2.319930  48.818460   
397     4.850520  45.768530   
398     2.237620  48.883280   
401     2.237620  48.883280   
403     4.902705  45.855110

In [8]:
# Step 2: Convert daily salaries to annual by multiplying by 252
daily_salaries = [100, 400, 480, 520, 550, 570, 600, 650]
df.loc[df["Salary Min"].isin(daily_salaries), "Salary Min"] *= 252
df.loc[df["Salary Max"].isin(daily_salaries), "Salary Max"] *= 252

In [9]:
# Check if Step 2 has been adjusted: YES
low_salaries = df[(df["Salary Min"] < 1000) | (df["Salary Max"] < 1000)]
low_salaries

Job Title                           Company  \
397              Data Scientist                             APRIL   
398              Data Scientist                        Canal Plus   
401              Data Scientist                        Canal Plus   
403              Data Scientist                         Framatome   
800               Data Engineer  Just People Information Security   
1350              Data Engineer                               NaN   
1356              Data Engineer            Jordan Human Resources   
1415  Machine Learning Engineer      CES Information Technologies   
1417  Machine Learning Engineer           SIlverPeople Consulting   
1629  Machine Learning Engineer            V R Della Infotech Inc   
2343              Data Engineer                               NaN   

                           Location  Salary Min  Salary Max  \
397          Caluire-et-Cuire, Lyon       486.0      1802.0   
398               Puteaux, Nanterre       486.0      1802.0   
401               Puteaux, Nanterre       486.0      1802.0   
403     Rhône, Auvergne-Rhône-Alpes       486.0      1802.0   
800       Brisbane, Brisbane Region         0.0    286000.0   
1350          Johannesburg, Gauteng         0.0     13200.0   
1356             Centurion, Tshwane        36.0        36.0   
1415           Hyderabad, Telangana         0.0   1500000.0   
1417            Mumbai, Maharashtra         0.0   2700000.0   
1629  Sunnyvale, Santa Clara County         2.0        61.0   
2343          Johannesburg, Gauteng         0.0     13200.0   

                                            Description Extracted Skills  \
397   Venez extraire, analyser et développer des alg...               []   
398   Plus précisément, vous intégrerez la direction...               []   
401   Plus précisément, vous intégrerez la direction...               []   
403   Framatome souhaite étendre sa capacité à trait...               []   
800   You will be a key part of delivering high qual...               []   
1350  Join a leading company pioneering the power of...               []   
1356  A client in the automobile industry is looking...               []   
1415  o Critical thinking mind who likes to solve co...               []   
1417  ML Engineer-Analyst/ Senior Analyst Job purpos...               []   
1629  Description: Description Job Title EA ML Engin...               []   
2343  Join a leading company pioneering the power of...               []   

       Longitude   Latitude  \
397     4.850520  45.768530   
398     2.237620  48.883280   
401     2.237620  48.883280   
403     4.902705  45.855110   
800   152.928532 -27.416056   
1350   28.026104 -26.183117   
1356   28.185860 -25.842500   
1415   78.508060  17.402750   
1417   72.844150  19.008210   
1629 -122.021940  37.376099   
2343   28.026104 -26.183117   

                                                    URL  ... Pandas  Power BI  \
397   https://www.adzuna.fr/details/5036975152?utm_m...  ...      0         0   
398   https://www.adzuna.fr/details/5076170998?utm_m...  ...      0         0   
401   https://www.adzuna.fr/details/5076171459?utm_m...  ...      0         0   
403   https://www.adzuna.fr/details/5080251351?utm_m...  ...      0         0   
800   https://www.adzuna.com.au/details/5079379477?u...  ...      0         0   
1350  https://www.adzuna.co.za/land/ad/5051267974?se...  ...      0         0   
1356  https://www.adzuna.co.za/details/5078585241?ut...  ...      0         0   
1415  https://www.adzuna.in/details/2658062217?utm_m...  ...      0         0   
1417  https://www.adzuna.in/details/2383302553?utm_m...  ...      0         0   
1629  https://www.adzuna.com/details/5080727251?utm_...  ...      0         0   
2343  https://www.adzuna.co.za/land/ad/5051267974?se...  ...      0         0   

     PyTorch  Python  R  SQL  Snowflake  Spark  Tableau  TensorFlow  
397        0       0  0    0          0      0        0           0  
398        0       0  0    0         

In [10]:
# Delete these 7 rows!
df = df[df["Salary Min"] >= 10000]
new_count = df.shape[0]
print(f"New total job listings after deletion: {new_count}")

New total job listings after deletion: 2364


In [11]:
df

Job Title        Company                        Location  \
0            Data Engineer  Catch Recruit     Sandton, North Johannesburg   
1            Data Engineer       TN Italy               Lombardia, Italia   
2           Data Scientist         Amazon  Provincia di Milano, Lombardia   
3           Data Scientist  ENGINEERINGUK  Provincia di Milano, Lombardia   
4           Data Scientist         Amazon  Provincia di Milano, Lombardia   
...                    ...            ...                             ...   
2417  Analytics Consultant     Link Group           Wrocław, dolnośląskie   
2418  Analytics Consultant     Link Group              Gdańsk, Trójmiasto   
2419  Analytics Consultant     Link Group           Warszawa, mazowieckie   
2420  Analytics Consultant     Link Group           Poznań, wielkopolskie   
2421  Analytics Consultant     Link Group             Kraków, małopolskie   

      Salary Min  Salary Max  \
0       240000.0    420000.0   
1        50000.0     70000.0   
2        50000.0     70000.0   
3        50000.0     70000.0   
4        50000.0     70000.0   
...          ...         ...   
2417     22680.0     23940.0   
2418     22680.0     23940.0   
2419     22680.0     23940.0   
2420     22680.0     23940.0   
2421     22680.0     23940.0   

                                            Description Extracted Skills  \
0     Key Responsibilities - Develop and maintain sc...               []   
1     Data Core Engineer - Milano/Roma/Napoli, Città...               []   
2     Regional Safety Engineer, Data Center Health a...               []   
3     Regional Safety Engineer, Data Center Health a...               []   
4     Regional Safety Engineer, Data Center Health a...               []   
...                                                 ...              ...   
2417  Chcesz pracować w dynamicznie rozwijającej się...               []   
2418  Chcesz pracować w dynamicznie rozwijającej się...               []   
2419  Chcesz pracować w dynamicznie rozwijającej się...               []   
2420  Chcesz pracować w dynamicznie rozwijającej się...               []   
2421  Chcesz pracować w dynamicznie rozwijającej się...               []   

      Longitude   Latitude                                                URL  \
0     28.048330 -26.068610  https://www.adzuna.co.za/details/5012435460?ut...   
1      9.574901  45.581846  https://www.adzuna.it/land/ad/5083569093?se=xq...   
2      9.138379  45.473082  https://www.adzuna.it/land/ad/5080642147?se=xq...   
3      9.138379  45.473082  https://www.adzuna.it/land/ad/4934765924?se=xq...   
4      9.138379  45.473082  https://www.adzuna.it/land/ad/4998300620?se=xq...   
...         ...        ...                                                ...   
2417  17.038540  51.107890  https://www.adzuna.pl/land/ad/5081135237?se=cq...   
2418  18.646640  54.352030  https://www.adzuna.pl/land/ad/5081135244?se=cq...   
2419  21.245300  52.215190  https://www.adzuna.pl/land/ad/5081135234?se=cq...   
2420  16.938750  52.403210  https://www.adzuna.pl/land/ad/5081135315?se=cq...   
2421  20.178480  50.102400  https://www.adzuna.pl/land/ad/5081135239?se=cq...   

      ... Pandas  Power BI PyTorch  Python  R  SQL  Snowflake  Spark  Tableau  \
0     ...      0         0       0       0  0    0          0      0        0   
1     ...      0         0       0       0  1    0          0      0        0   
2     ...      0         0       0       0  0    0          0      0        0   
3     ...      0         0       0       0  0    0          0      0        0   
4     ...      0         0       0       0  0    0          0      0        0   
...   ...    ...       ...     ...     ... ..  ...        ...    ...      ...   
2417  ...      0         0       0       0  0    1          0      0        0   
2418  ...      0         0       0       0  0    1          0      0        0   
2419  ...      0         0       0       0  0    1          0      0        0   
2420  ...  

In [73]:
# Step 4: Standardize Currency to USD (assuming all values are in local currencies)
# Conversion rates (Example: You can update based on real-time rates)
currency_conversion = {
    "pl": 0.25,  # Polish Zloty to USD
    "it": 1.09,  # Euro to USD
    "fr": 1.09,  # Euro to USD
    "es": 1.09,  # Euro to USD
    "de": 1.09,  # Euro to USD
    "gb": 1.26,  # British Pound to USD
    "au": 0.66,  # Australian Dollar to USD
    "ca": 0.74,  # Canadian Dollar to USD
    "in": 0.012, # Indian Rupee to USD
    "za": 0.054, # South African Rand to USD
    "mx": 0.056,  # Mexican Peso to USD
    "at": 1.09,  # Austria (Euro)
    "be": 1.09,  # Belgium (Euro)
    "br": 0.20,  # Brazil (Brazilian Real to USD)
    "ch": 1.12,  # Switzerland (Swiss Franc to USD)
    "nl": 1.09,  # Netherlands (Euro)
    "nz": 0.61,  # New Zealand (NZD to USD)
    "sg": 0.74   # Singapore (SGD to USD)
}

In [74]:
# Function to extract country code from URL and apply conversion
def convert_salary_using_url(row):
    url = str(row["URL"])
    salary_min = row["Salary Min"]
    salary_max = row["Salary Max"]
    
    # Extract country code from the domain using regex (handle .co.za and .co.uk separately)
    match = re.search(r'adzuna\.([a-z]{2,3})/', url)
    country_code = match.group(1) if match else "us"  # Default to USD if no match
    
    # Adjust for unique domain structures
    if "adzuna.co.za" in url:
        country_code = "za"
    elif "adzuna.co.uk" in url:
        country_code = "gb"
    elif "adzuna.com.au" in url:
        country_code = "au"
    
    # Get conversion rate (default to 1 if country not found)
    conversion_rate = currency_conversion.get(country_code, 1)
    
    # Convert salaries to USD
    return round(salary_min * conversion_rate, 2), round(salary_max * conversion_rate, 2) if pd.notna(salary_max) else None


In [75]:
# Apply conversion function
df[["Salary Min", "Salary Max"]] = df.apply(convert_salary_using_url, axis=1, result_type="expand")

In [76]:
df

Job Title  \
0                 Data Engineer   
1                 Data Engineer   
2                Data Scientist   
3                Data Scientist   
4                Data Scientist   
5                Data Scientist   
6     Machine Learning Engineer   
7                 Data Engineer   
8                 Data Engineer   
9                 Data Engineer   
10    Machine Learning Engineer   
11               Data Scientist   
12               Data Scientist   
13                Data Engineer   
14                Data Engineer   
15                Data Engineer   
16                Data Engineer   
17                 Data Analyst   
18         Analytics Consultant   
19         Analytics Consultant   
20         Analytics Consultant   
21         Analytics Consultant   
22               Data Scientist   
23                Data Engineer   
24                Data Engineer   
25               Data Scientist   
26               Data Scientist   
27               Data Scientist   
28               Data Scientist   
29               Data Scientist   
30               Data Scientist   
31                 Data Analyst   
32               Data Scientist   
33               Data Scientist   
34               Data Scientist   
35                 Data Analyst   
36    Machine Learning Engineer   
37               Data Scientist   
38                Data Engineer   
39                Data Engineer   
40    Machine Learning Engineer   
41         Analytics Consultant   
42               Data Scientist   
43    Machine Learning Engineer   
44    Machine Learning Engineer   
45    Machine Learning Engineer   
46    Machine Learning Engineer   
47    Machine Learning Engineer   
48    Machine Learning Engineer   
49               Data Scientist   
53               Data Scientist   
54                 Data Analyst   
55                 Data Analyst   
56    Machine Learning Engineer   
57                 Data Analyst   
58                Data Engineer   
59                Data Engineer   
60               Data Scientist   
61               Data Scientist   
62               Data Scientist   
63                 Data Analyst   
64               Data Scientist   
65               Data Scientist   
66                 Data Analyst   
67                 Data Analyst   
68                 Data Analyst   
69                Data Engineer   
70                 Data Analyst   
71                Data Engineer   
72                Data Engineer   
73                Data Engineer   
74                Data Engineer   
75                 Data Analyst   
76         Analytics Consultant   
77                Data Engineer   
78                 Data Analyst   
79               Data Scientist   
80               Data Scientist   
81               Data Scientist   
82    Machine Learning Engineer   
83               Data Scientist   
84               Data Scientist   
85               Data Scientist   
86                Data Engineer   
87                Data Engineer   
88                Data Engineer   
89                Data Engineer   
90                Data Engineer   
91               Data Scientist   
92                Data Engineer   
93                Data Engineer   
94                Data Engineer   
95                Data Engineer   
96               Data Scientist   
97               Data Scientist   
98               Data Scientist   
99               Data Scientist   
100   Machine Learning Engineer   
101               Data Engineer   
102               Data Engineer   
103               Data Engineer   
104               Data Engineer   
108               Data Engineer   
109   Machine Learning Engineer   
110               Data Engineer   
111              Data Scientist   
113   Machine Learning Engineer   
114               Data Engineer   
115               Data Engineer   
116               Data Engineer   
117               Data Engineer   
118   Machine Learning Engineer   
119   Machine Learning Engineer   
120   Machine Learning Engineer 

In [77]:
# Count job listings where Salary Min is below 10,000
low_salary_count = df[df["Salary Min"] < 10000].shape[0]
print(f"Number of job listings where Salary Min is below 10,000: {low_salary_count}")


Number of job listings where Salary Min is below 10,000: 47


In [78]:
# Delete these 47 Job listings.
df = df[df["Salary Min"] >= 10000]

In [79]:
df.describe()

Salary Min     Salary Max    Longitude     Latitude  \
count    2317.000000    2316.000000  2317.000000  2317.000000   
mean    79779.911731   93717.194072   -16.614265    40.581493   
std     41980.097861   45786.624766    56.884800    20.359173   
min     10500.000000   12000.000000  -157.846500   -37.844856   
25%     50458.440000   63000.000000   -75.566083    38.970000   
50%     70500.000000   82948.475000     0.131237    45.473082   
75%    100960.000000  114000.000000    16.938750    51.523772   
max    278460.000000  566800.000000   174.763300    58.299755   

       Experience_years   Apache Airflow        Azure     Big Data  \
count       2317.000000      2317.000000  2317.000000  2317.000000   
mean           3.151057         0.001295     0.011653     0.011221   
std            3.457560         0.035967     0.107341     0.105358   
min            0.000000         0.000000     0.000000     0.000000   
25%            1.000000         0.000000     0.000000     0.000000   
50%            2.000000         0.000000     0.000000     0.000000   
75%            5.000000         0.000000     0.000000     0.000000   
max           15.000000         1.000000     1.000000     1.000000   

        Data Pipelines   Deep Learning  ...       Pandas     Power BI  \
count      2317.000000     2317.000000  ...  2317.000000  2317.000000   
mean          0.023738        0.002590  ...     0.001295     0.032369   
std           0.152263        0.050833  ...     0.035967     0.177017   
min           0.000000        0.000000  ...     0.000000     0.000000   
25%           0.000000        0.000000  ...     0.000000     0.000000   
50%           0.000000        0.000000  ...     0.000000     0.000000   
75%           0.000000        0.000000  ...     0.000000     0.000000   
max           1.000000        1.000000  ...     1.000000     1.000000   

           PyTorch       Python            R          SQL    Snowflake  \
count  2317.000000  2317.000000  2317.000000  2317.000000  2317.000000   
mean      0.000432     0.055244     0.058265     0.060423     0.007769   
std       0.020775     0.228505     0.234294     0.238320     0.087816   
min       0.000000     0.000000     0.000000     0.000000     0.000000   
25%       0.000000     0.000000     0.000000     0.000000     0.000000   
50%       0.000000     0.000000     0.000000     0.000000     0.000000   
75%       0.000000     0.000000     0.000000     0.000000     0.000000   
max       1.000000     1.000000     1.000000     1.000000     1.000000   

             Spark      Tableau   TensorFlow  
count  2317.000000  2317.000000  2317.000000  
mean      0.002590     0.005179     0.000432  
std       0.050833     0.071795     0.020775  
min       0.000000     0.000000     0.000000  
25%       0.000000     0.000000     0.000000  
50%       0.000000     0.000000     0.000000  
75%       0.000000     0.000000     0.000000  
max       1.000000     1.000000     1.000000  

[8 rows x 56 columns]

In [80]:
df

Job Title  \
0                 Data Engineer   
1                 Data Engineer   
2                Data Scientist   
3                Data Scientist   
4                Data Scientist   
5                Data Scientist   
6     Machine Learning Engineer   
7                 Data Engineer   
8                 Data Engineer   
9                 Data Engineer   
10    Machine Learning Engineer   
11               Data Scientist   
12               Data Scientist   
13                Data Engineer   
14                Data Engineer   
15                Data Engineer   
16                Data Engineer   
17                 Data Analyst   
18         Analytics Consultant   
19         Analytics Consultant   
20         Analytics Consultant   
21         Analytics Consultant   
22               Data Scientist   
23                Data Engineer   
24                Data Engineer   
25               Data Scientist   
26               Data Scientist   
27               Data Scientist   
28               Data Scientist   
29               Data Scientist   
30               Data Scientist   
31                 Data Analyst   
32               Data Scientist   
33               Data Scientist   
34               Data Scientist   
35                 Data Analyst   
36    Machine Learning Engineer   
37               Data Scientist   
38                Data Engineer   
39                Data Engineer   
40    Machine Learning Engineer   
41         Analytics Consultant   
42               Data Scientist   
43    Machine Learning Engineer   
44    Machine Learning Engineer   
45    Machine Learning Engineer   
46    Machine Learning Engineer   
47    Machine Learning Engineer   
48    Machine Learning Engineer   
49               Data Scientist   
53               Data Scientist   
56    Machine Learning Engineer   
57                 Data Analyst   
58                Data Engineer   
59                Data Engineer   
60               Data Scientist   
61               Data Scientist   
62               Data Scientist   
63                 Data Analyst   
64               Data Scientist   
65               Data Scientist   
66                 Data Analyst   
67                 Data Analyst   
68                 Data Analyst   
69                Data Engineer   
70                 Data Analyst   
71                Data Engineer   
72                Data Engineer   
73                Data Engineer   
74                Data Engineer   
75                 Data Analyst   
76         Analytics Consultant   
77                Data Engineer   
78                 Data Analyst   
79               Data Scientist   
80               Data Scientist   
81               Data Scientist   
82    Machine Learning Engineer   
83               Data Scientist   
84               Data Scientist   
85               Data Scientist   
86                Data Engineer   
87                Data Engineer   
88                Data Engineer   
89                Data Engineer   
90                Data Engineer   
91               Data Scientist   
92                Data Engineer   
93                Data Engineer   
94                Data Engineer   
95                Data Engineer   
96               Data Scientist   
97               Data Scientist   
98               Data Scientist   
99               Data Scientist   
100   Machine Learning Engineer   
101               Data Engineer   
102               Data Engineer   
103               Data Engineer   
104               Data Engineer   
108               Data Engineer   
109   Machine Learning Engineer   
110               Data Engineer   
111              Data Scientist   
113   Machine Learning Engineer   
114               Data Engineer   
115               Data Engineer   
116               Data Engineer   
117               Data Engineer   
118   Machine Learning Engineer   
119   Machine Learning Engineer   
120   Machine Learning Engineer   
121   Machine Learning Engineer   
122   Machine Learning Engineer 

In [81]:
pd.set_option("display.max_rows", None)
filtered_df = df[df["Company"].str.lower().isin(["link group", "provectus", "softeq"])]
filtered_df

Job Title     Company               Location  \
495              Data Scientist  Link Group  Warszawa, mazowieckie   
496              Data Scientist  Link Group  Warszawa, mazowieckie   
1109              Data Engineer  Link Group    Kraków, małopolskie   
1110              Data Engineer  Link Group     Gdańsk, Trójmiasto   
1111              Data Engineer  Link Group  Warszawa, mazowieckie   
1112              Data Engineer  Link Group  Wrocław, dolnośląskie   
1115              Data Engineer  Link Group  Poznań, wielkopolskie   
1116              Data Engineer  Link Group  Wrocław, dolnośląskie   
1117              Data Engineer  Link Group      Katowice, śląskie   
1118              Data Engineer  Link Group  Warszawa, mazowieckie   
1119              Data Engineer  Link Group     Gdańsk, Trójmiasto   
1121              Data Engineer  Link Group    Kraków, małopolskie   
1137              Data Engineer  Link Group  Wrocław, dolnośląskie   
1138              Data Engineer  Link Group    Kraków, małopolskie   
1139              Data Engineer  Link Group  Poznań, wielkopolskie   
1140              Data Engineer  Link Group  Warszawa, mazowieckie   
1141              Data Engineer  Link Group     Gdańsk, Trójmiasto   
1147              Data Engineer   Provectus  Wrocław, dolnośląskie   
1155              Data Engineer  Link Group     Gdańsk, Trójmiasto   
1156              Data Engineer  Link Group  Poznań, wielkopolskie   
1157              Data Engineer  Link Group  Wrocław, dolnośląskie   
1158              Data Engineer  Link Group    Kraków, małopolskie   
1159              Data Engineer  Link Group  Wrocław, dolnośląskie   
1160              Data Engineer  Link Group  Poznań, wielkopolskie   
1161              Data Engineer  Link Group  Warszawa, mazowieckie   
1162              Data Engineer  Link Group  Warszawa, mazowieckie   
1163              Data Engineer  Link Group     Gdańsk, Trójmiasto   
1171              Data Engineer  Link Group  Poznań, wielkopolskie   
1172              Data Engineer  Link Group  Warszawa, mazowieckie   
1173              Data Engineer  Link Group     Gdańsk, Trójmiasto   
1174              Data Engineer  Link Group    Kraków, małopolskie   
1175              Data Engineer  Link Group  Wrocław, dolnośląskie   
1463  Machine Learning Engineer      Softeq  Wrocław, dolnośląskie   
1464  Machine Learning Engineer      Softeq  Warszawa, mazowieckie   
1465  Machine Learning Engineer      Softeq    Kraków, małopolskie   
1466  Machine Learning Engineer      Softeq     Gdańsk, Trójmiasto   
1832             Data Scientist  Link Group  Warszawa, mazowieckie   
1833             Data Scientist  Link Group  Warszawa, mazowieckie   
2133              Data Engineer  Link Group    Kraków, małopolskie   
2134              Data Engineer  Link Group     Gdańsk, Trójmiasto   
2135              Data Engineer  Link Group  Warszawa, mazowieckie   
2136              Data Engineer  Link Group  Wrocław, dolnośląskie   
2139              Data Engineer  Link Group  Poznań, wielkopolskie   
2140              Data Engineer  Link Group  Wrocław, dolnośląskie   
2141              Data Engineer  Link Group      Katowice, śląskie   
2142              Data Engineer  Link Group  Warszawa, mazowieckie   
2143              Data Engineer  Link Group     Gdańsk, Trójmiasto   
2145              Data Engineer  Link Group    Kraków, małopolskie   
2161              Data Engineer  Link Group  Wrocław, dolnośląskie   
2162              Data Engineer  Link Group    Kraków, małopolskie   
2163              Data Engineer  Link Group  Poznań, wielkopolskie   
2164              Data Engineer  Link Group  Warszawa, mazowieckie   
2165              Data Engineer  Link Group     Gdańsk, Trójmiasto   
2171              Data Engineer   Provectus  Wrocław, dolnośląskie   
2179              Data Engineer  Link Group     Gdańsk, Trójmiasto   
2180              Data Engineer  Link Group  Poznań, wielkopolskie   
2181              Data Engineer 

In [82]:
# The LinkGroup, able.Tech, Softeq and Provectus Jobs are monthly, and need to be converted into yearly salaries:
companies = ["link group", "softeq", "provectus"]
df.loc[(df["Company"].str.lower().isin(companies)) & (df["Salary Max"] < 28000), "Salary Max"] *= 12


In [83]:
# Check if this has been done:
pd.set_option("display.max_rows", None)
filtered_df = df[df["Company"].str.lower().isin(["link group", "provectus", "softeq"])]
filtered_df

Job Title     Company               Location  \
495              Data Scientist  Link Group  Warszawa, mazowieckie   
496              Data Scientist  Link Group  Warszawa, mazowieckie   
1109              Data Engineer  Link Group    Kraków, małopolskie   
1110              Data Engineer  Link Group     Gdańsk, Trójmiasto   
1111              Data Engineer  Link Group  Warszawa, mazowieckie   
1112              Data Engineer  Link Group  Wrocław, dolnośląskie   
1115              Data Engineer  Link Group  Poznań, wielkopolskie   
1116              Data Engineer  Link Group  Wrocław, dolnośląskie   
1117              Data Engineer  Link Group      Katowice, śląskie   
1118              Data Engineer  Link Group  Warszawa, mazowieckie   
1119              Data Engineer  Link Group     Gdańsk, Trójmiasto   
1121              Data Engineer  Link Group    Kraków, małopolskie   
1137              Data Engineer  Link Group  Wrocław, dolnośląskie   
1138              Data Engineer  Link Group    Kraków, małopolskie   
1139              Data Engineer  Link Group  Poznań, wielkopolskie   
1140              Data Engineer  Link Group  Warszawa, mazowieckie   
1141              Data Engineer  Link Group     Gdańsk, Trójmiasto   
1147              Data Engineer   Provectus  Wrocław, dolnośląskie   
1155              Data Engineer  Link Group     Gdańsk, Trójmiasto   
1156              Data Engineer  Link Group  Poznań, wielkopolskie   
1157              Data Engineer  Link Group  Wrocław, dolnośląskie   
1158              Data Engineer  Link Group    Kraków, małopolskie   
1159              Data Engineer  Link Group  Wrocław, dolnośląskie   
1160              Data Engineer  Link Group  Poznań, wielkopolskie   
1161              Data Engineer  Link Group  Warszawa, mazowieckie   
1162              Data Engineer  Link Group  Warszawa, mazowieckie   
1163              Data Engineer  Link Group     Gdańsk, Trójmiasto   
1171              Data Engineer  Link Group  Poznań, wielkopolskie   
1172              Data Engineer  Link Group  Warszawa, mazowieckie   
1173              Data Engineer  Link Group     Gdańsk, Trójmiasto   
1174              Data Engineer  Link Group    Kraków, małopolskie   
1175              Data Engineer  Link Group  Wrocław, dolnośląskie   
1463  Machine Learning Engineer      Softeq  Wrocław, dolnośląskie   
1464  Machine Learning Engineer      Softeq  Warszawa, mazowieckie   
1465  Machine Learning Engineer      Softeq    Kraków, małopolskie   
1466  Machine Learning Engineer      Softeq     Gdańsk, Trójmiasto   
1832             Data Scientist  Link Group  Warszawa, mazowieckie   
1833             Data Scientist  Link Group  Warszawa, mazowieckie   
2133              Data Engineer  Link Group    Kraków, małopolskie   
2134              Data Engineer  Link Group     Gdańsk, Trójmiasto   
2135              Data Engineer  Link Group  Warszawa, mazowieckie   
2136              Data Engineer  Link Group  Wrocław, dolnośląskie   
2139              Data Engineer  Link Group  Poznań, wielkopolskie   
2140              Data Engineer  Link Group  Wrocław, dolnośląskie   
2141              Data Engineer  Link Group      Katowice, śląskie   
2142              Data Engineer  Link Group  Warszawa, mazowieckie   
2143              Data Engineer  Link Group     Gdańsk, Trójmiasto   
2145              Data Engineer  Link Group    Kraków, małopolskie   
2161              Data Engineer  Link Group  Wrocław, dolnośląskie   
2162              Data Engineer  Link Group    Kraków, małopolskie   
2163              Data Engineer  Link Group  Poznań, wielkopolskie   
2164              Data Engineer  Link Group  Warszawa, mazowieckie   
2165              Data Engineer  Link Group     Gdańsk, Trójmiasto   
2171              Data Engineer   Provectus  Wrocław, dolnośląskie   
2179              Data Engineer  Link Group     Gdańsk, Trójmiasto   
2180              Data Engineer  Link Group  Poznań, wielkopolskie   
2181              Data Engineer 

In [84]:
df.to_csv("Cleaned_Salary_Data_and_Title_and_Skills_Final.csv", index=False)
